# Overview
In this notebook isoforms are filtered by their length (retaining the longest isoform for each genome). 
Then homologous groups are parsed and alignments inferred, after which phylogenetic tree inference is done. In order to be able to run subsequent analyses, dummy (i.e., fictiocious) phylogenetic trees are generated for specific cases.

In [1]:
import pandas as pd

platys_data = pd.read_csv('../data/species_Platyhelminthes--___.csv')

In [2]:
platys_data.head()

Species Name  \
0  Atriophallophorus winterbourni   
1             Clonorchis sinensis   
2             Clonorchis sinensis   
3         Dibothriocephalus latus   
4        Dicrocoelium dendriticum   

                                          Provider                 Assembly  \
0  Swiss Federal Institute of Technology in Zurich             ASM1340708v1   
1                           Sun Yat-sen University           C_sinensis-2.0   
2                      The University of Melbourne                  CSKR.v2   
3                        Wellcome Sanger Institute  D_latum_Geneva_0011_upd   
4                        Wellcome Sanger Institute             tdDicDend1.1   

  BioProject ID                Clade     Genome Browser          N50  \
0   PRJNA636673   Trematoda (Flukes)  JBrowse | Ensembl       39,978   
1    PRJDA72781   Trematoda (Flukes)  JBrowse | Ensembl      415,842   
2   PRJNA386618   Trematoda (Flukes)  JBrowse | Ensembl  168,711,085   
3     PRJEB1206  Cestoda (Tapeworms)  JBrowse | Ensembl        6,726   
4    PRJEB44434   Trematoda (Flukes)  JBrowse | Ensembl  117,106,881   

     Genome Size Number of Scaffolds Number of Coding Genes  
0    601,728,533              26,114                 11,499  
1    547,288,241               4,348                 13,634  
2    558,124,894                  78                 13,489  
3    531,434,409             140,294                 19,966  
4  1,889,995,958              19,456                 13,685

# Filtering by isoform length

In [31]:
import rpy2, tqdm # this was run in another server, thats why following lines appear

ModuleNotFoundError: No module named 'rpy2'

In [16]:
%load_ext rpy2.ipython

In [20]:
%R library(orthologr)

R[write to console]: Loading required package: data.table

R[write to console]: data.table 1.15.2 using 2 threads (see ?getDTthreads).  
R[write to console]: Latest news: r-datatable.com



array(['orthologr', 'data.table', 'tools', 'stats', 'graphics',
       'grDevices', 'utils', 'datasets', 'methods', 'base'], dtype='<U10')

In [15]:
%%bash

ls ../data/platyhelminthes_dataset_vfinal/*

../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJDA72781.WBPS18.annotations.gff3.gz
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJDA72781.WBPS18.canonical_geneset.gtf.gz
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJDA72781.WBPS18.protein.fa.gz
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJDA72781.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJNA386618.WBPS18.canonical_geneset.gtf.gz
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJNA386618.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/echinococcus_canadensis.PRJEB8992.WBPS18.canonical_geneset.gtf.gz
../data/platyhelminthes_dataset_vfinal/echinococcus_canadensis.PRJEB8992.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/echinococcus_granulosus.PRJEB121.WBPS18.canonical_geneset.gtf.gz
../data/platyhelminthes_dataset_vfinal/echinococcus_granulosus.PRJEB121.WBPS

In [38]:
for protein_file in tqdm.tqdm(glob.glob('../data/platyhelminthes_dataset_vfinal/*.protein*')):
    annotation_file = protein_file.replace('.protein.fa.gz', '.canonical_geneset.gtf.gz')
    new_protein_file = protein_file.rpartition('.fa.gz')[0]+'.longest_isoforms.faa'
    rpy2.robjects.globalenv['protein_file'] = protein_file
    rpy2.robjects.globalenv['annotation_file'] = annotation_file
    rpy2.robjects.globalenv['new_protein_file'] = new_protein_file
    rpy2.robjects.r("retrieve_longest_isoforms(proteome_file = protein_file, annotation_file = annotation_file, new_file = new_protein_file, annotation_format = 'gtf')")

  0%|                                                                                                                                  | 0/24 [00:00<?, ?it/s]R[write to console]: Extracting longest isoform from hymenolepis_microstoma.PRJEB124.WBPS18.protein.fa.gz ...

R[write to console]: Importing proteome file hymenolepis_microstoma.PRJEB124.WBPS18.protein.fa.gz ...

R[write to console]: Importing '../data/platyhelminthes_dataset_vfinal/hymenolepis_microstoma.PRJEB124.WBPS18.canonical_geneset.gtf.gz' ...

R[write to console]: Importing gtf file hymenolepis_microstoma.PRJEB124.WBPS18.canonical_geneset.gtf.gz ...

R[write to console]: Filter for gene_biotype == 'protein_coding' AND type == 'transcript' ...

R[write to console]: After filtering, the gtf file includes 11429 rows.

R[write to console]: Join transcript_ids from FASTA header with transcript_ids from GTF annotation file ...

R[write to console]: The joined file contains 11429 rows.

R[write to console]: Removing rows with NA

|===================================================== |100% ~0 s remainingg                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

R[write to console]: 


R[write to console]: Writing 10139 unique longest peptide sequences (from initially 11429 isoforms) to new fasta file ../data/platyhelminthes_dataset_vfinal/hymenolepis_microstoma.PRJEB124.WBPS18.protein.longest_isoforms.faa ...

R[write to console]: Retrieval finished successfully.

  4%|█████                                                                                                                     | 1/24 [00:27<10:23, 27.10s/it]R[write to console]: Extracting longest isoform from schistosoma_margrebowiei.PRJEB44434.WBPS18.protein.fa.gz ...

R[write to console]: Importing proteome file schistosoma_margrebowiei.PRJEB44434.WBPS18.protein.fa.gz ...

R[write to console]: Importing '../data/platyhelminthes_dataset_vfinal/schistosoma_margrebowiei.PRJEB44434.WBPS18.canonical_geneset.gtf.gz' ...

R[write to console]: Importing gtf file schistosoma_margrebowiei.PRJEB44434.WBPS18.canonical_geneset.gtf.gz ...

R[write to console]: Filter for gene_biotype == 'prot

|===================================================== |100% ~0 s remainingg                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

R[write to console]: 


R[write to console]: Writing 9780 unique longest peptide sequences (from initially 19527 isoforms) to new fasta file ../data/platyhelminthes_dataset_vfinal/schistosoma_margrebowiei.PRJEB44434.WBPS18.protein.longest_isoforms.faa ...

R[write to console]: Retrieval finished successfully.

  8%|██████████▏                                                                                                               | 2/24 [00:56<10:26, 28.46s/it]R[write to console]: Extracting longest isoform from taenia_solium.PRJNA170813.WBPS18.protein.fa.gz ...

R[write to console]: Importing proteome file taenia_solium.PRJNA170813.WBPS18.protein.fa.gz ...

R[write to console]: Importing '../data/platyhelminthes_dataset_vfinal/taenia_solium.PRJNA170813.WBPS18.canonical_geneset.gtf.gz' ...

R[write to console]: Importing gtf file taenia_solium.PRJNA170813.WBPS18.canonical_geneset.gtf.gz ...

R[write to console]: Filter for gene_biotype == 'protein_coding' AND type == 'transcript' 

...

R[write to console]: 


R[write to console]: Writing 10084 unique longest peptide sequences (from initially 20253 isoforms) to new fasta file ../data/platyhelminthes_dataset_vfinal/schistosoma_curassoni.PRJEB44434.WBPS18.protein.longest_isoforms.faa ...

R[write to console]: Retrieval finished successfully.

 92%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████▉          | 22/24 [13:46<01:07, 33.56s/it]R[write to console]: Extracting longest isoform from clonorchis_sinensis.PRJNA386618.WBPS18.protein.fa.gz ...

R[write to console]: Importing proteome file clonorchis_sinensis.PRJNA386618.WBPS18.protein.fa.gz ...

R[write to console]: Importing '../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJNA386618.WBPS18.canonical_geneset.gtf.gz' ...

R[write to console]: Importing gtf file clonorchis_sinensis.PRJNA386618.WBPS18.canonical_geneset.gtf.gz ...

R[write to console]: Filter for gene_biotype == 'protein_coding' AND

|===================================================== |100% ~0 s remainingg                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

R[write to console]: 


R[write to console]: Writing 13489 unique longest peptide sequences (from initially 14408 isoforms) to new fasta file ../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJNA386618.WBPS18.protein.longest_isoforms.faa ...

R[write to console]: Retrieval finished successfully.

 96%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉     | 23/24 [14:26<00:35, 35.44s/it]R[write to console]: Extracting longest isoform from schistosoma_haematobium.PRJNA78265.WBPS18.protein.fa.gz ...

R[write to console]: Importing proteome file schistosoma_haematobium.PRJNA78265.WBPS18.protein.fa.gz ...

R[write to console]: Importing '../data/platyhelminthes_dataset_vfinal/schistosoma_haematobium.PRJNA78265.WBPS18.canonical_geneset.gtf.gz' ...

R[write to console]: Importing gtf file schistosoma_haematobium.PRJNA78265.WBPS18.canonical_geneset.gtf.gz ...

R[write to console]: Filter for gene_biotype == 'protein_

|===================================================== |100% ~0 s remainingg                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

R[write to console]: 


R[write to console]: Writing 9431 unique longest peptide sequences (from initially 14700 isoforms) to new fasta file ../data/platyhelminthes_dataset_vfinal/schistosoma_haematobium.PRJNA78265.WBPS18.protein.longest_isoforms.faa ...

R[write to console]: Retrieval finished successfully.

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 24/24 [14:59<00:00, 37.49s/it]


In [2]:
target_genomes = ['fasciola_hepatica.PRJEB25283.WBPS18',
 'schistosoma_japonicum.PRJNA520774.WBPS18',
 'echinococcus_granulosus.PRJEB121.WBPS18',
 'opisthorchis_viverrini.PRJNA222628.WBPS18',
 'schistosoma_curassoni.PRJEB44434.WBPS18',
 'trichobilharzia_regenti.PRJEB44434.WBPS18',
 'taenia_asiatica.PRJNA299871.WBPS18',
 'clonorchis_sinensis.PRJNA386618.WBPS18',
 'macrostomum_lignano.PRJNA371498.WBPS18',
 'mesocestoides_corti.PRJEB510.WBPS18',
 'schistosoma_haematobium.PRJNA78265.WBPS18',
 'schistosoma_mansoni.PRJEA36577.WBPS18',
 'hymenolepis_diminuta.PRJEB30942.WBPS18',
 'taenia_saginata.PRJNA71493.WBPS18',
 'echinococcus_canadensis.PRJEB8992.WBPS18',
 'echinococcus_multilocularis.PRJEB122.WBPS18',
 'schistosoma_margrebowiei.PRJEB44434.WBPS18',
 'schmidtea_mediterranea.PRJNA12585.WBPS18',
 'taenia_solium.PRJNA170813.WBPS18',
 'schistosoma_mattheei.PRJEB44434.WBPS18',
 'hymenolepis_microstoma.PRJEB124.WBPS18']

In [3]:
len(target_genomes)

21

In [44]:
for file in glob.glob('../data/platyhelminthes_dataset_vfinal/*isoform*'):
    label = file.rpartition('/')[2].split('.')[0]+'_'+file.rpartition('/')[2].split('.')[1]
    if label in target_genomes:
        %system cp {file} ../

../data/platyhelminthes_dataset_vfinal/schmidtea_mediterranea.PRJNA12585.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/echinococcus_multilocularis.PRJEB122.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/schistosoma_margrebowiei.PRJEB44434.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/mesocestoides_corti.PRJEB510.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/schistosoma_mansoni.PRJEA36577.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/taenia_asiatica.PRJNA299871.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/echinococcus_granulosus.PRJNA182977.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/clonorchis_sinensis.PRJDA72781.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_dataset_vfinal/trichobilharzia_regenti.PRJEB44434.WBPS18.protein.longest_isoforms.faa
../data/platyhelminthes_data

https://drostlab.github.io/orthologr/reference/retrieve_longest_isoforms.html

# Renaming set of proteins

In [8]:
# create species to code dictionary
species2code = {species: species.split(' ')[0][0]+species.split(' ')[1][0:3].lower() for species in platys_data['Species Name'].to_list()} # create a dictionary species-code
# load all proteins into a dictionary (label as key, Biopython SeqRecord as object)
# rename all proteins using the codes in species2code dic
# each protein is named as <code>.<num>, increasing number from 1 to n (n = proteome size)

In [11]:
import glob, gzip, tqdm
from Bio import SeqIO

# create species to code dictionary
species2code = {species: species.split(' ')[0][0]+species.split(' ')[1][0:3].lower() for species in platys_data['Species Name'].to_list()}
# Create an empty list to store original and new protein names
correlation_data = []
# Load all proteins into a dictionary
protein_dict = {}
selected_protein_transcripts = {}

protein_files = glob.glob('../data/platyhelminthes_dataset_vfinal/*protein*isoforms*.faa')
for file in tqdm.tqdm(protein_files):
    species_name = file.rpartition('/')[2].split('.')[0].split('_')[0].title() + ' ' + file.rpartition('/')[2].split('.')[0].split('_')[1]
    code = species2code.get(species_name)
    if code:
        selected_protein_transcripts.update({code: []})
        with open(file, 'rt') as f:
            records = SeqIO.parse(f, "fasta")
            for i, record in enumerate(records, start=1):
                original_name = record.id
                new_name = f"{code}.{i}"
                code_selected_protein_transcripts = selected_protein_transcripts.get(code)
                code_selected_protein_transcripts.append(record.description)
                selected_protein_transcripts[code] = code_selected_protein_transcripts
                correlation_data.append({'Original Name': original_name, 'New Name': new_name})
                record.id = new_name
                record.name = new_name
                record.description = new_name
                protein_dict[new_name] = record


100%|██████████| 21/21 [00:04<00:00,  4.75it/s]


In [29]:
# creating a correlation table to save
original2new = pd.DataFrame.from_dict(correlation_data)

In [30]:
original2new.to_csv('../results/misc/gene_code_correspondance.tsv', sep = '\t', index = False)

In [70]:
import os

In [81]:
for target_genome in tqdm.tqdm(target_genomes):
    species = target_genome.rpartition('.')[0].split('_')[0].title() + ' ' + target_genome.rpartition('.')[0].split('_')[1].rpartition('.')[0]
    code = species2code.get(species)
    records = [record for recordid,record in protein_dict.items() if recordid.rpartition('.')[0] == code]
    proteome_name = f'../data/platyhelminthes_dataset/{target_genome}.protein.longest_isoforms.faa'
    if not os.path.exists(proteome_name):
        with open(proteome_name, 'a') as f:
            SeqIO.write(records, proteome_name, 'fasta')

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 23/23 [00:02<00:00, 10.93it/s]


## Get selected isoforms for CDS transcripts

In [3]:
import glob, os
import pandas as pd

In [4]:
original2new = pd.read_csv('../results/misc/gene_code_correspondance.tsv', sep = '\t')

In [5]:
original2new

Original Name    New Name
0       TsM_000000100      Tsol.1
1       TsM_000000200      Tsol.2
2       TsM_000000300      Tsol.3
3       TsM_000000400      Tsol.4
4       TsM_000000500      Tsol.5
...               ...         ...
304155     T265_16376  Oviv.16375
304156     T265_16377  Oviv.16376
304157     T265_16378  Oviv.16377
304158     T265_16379  Oviv.16378
304159     T265_16380  Oviv.16379

[304160 rows x 2 columns]

In [6]:
code2species = {
    'Tsol': 'T. solium',
    'Mlig': 'M. lignano',
    'Treg': 'T. regenti',
    'Hmic': 'H. microstoma',
    'Tsag': 'T. saginata',
    'Hdim': 'H. diminuta',
    'Fhep': 'F. hepatica',
    'Smat': 'S. mattheei',
    'Scur': 'S. curassoni',
    'Emul': 'E. multilocularis',
    'Sman': 'S. mansoni',
    'Tasi': 'T. asiatica',
    'Smar': 'S. margrebowiei',
    'Csin': 'C. sinensis',
    'Egra': 'E. granulosus',
    'Mcor': 'M. corti',
    'Shae': 'S. haematobium',
    'Sjap': 'S. japonicum',
    'Ecan': 'E. canadensis',
    'Smed': 'S. mediterranea',
    'Oviv': 'O. viverrini'
}

In [10]:
import gtfparse

In [34]:
import gzip
import glob
import os

directory_path = '../data/platyhelminthes_dataset_vfinal/'
gtf_files = glob.glob(os.path.join(directory_path, '*canonical*.gtf.gz'))

def parse_attributes(attributes_str):
    """Parse the attributes column of a GTF file into a dictionary."""
    attributes = {}
    for attribute in attributes_str.split(';'):
        attribute = attribute.strip()
        if not attribute:
            continue
        key, value = attribute.split(' ', 1)
        value = value.strip('"')
        attributes[key] = value
    return attributes

def find_longest_cds(gtf_file):
    cds_lengths = {}
    with gzip.open(gtf_file, "rt") as handle:
        for line in handle:
            if line.startswith("#"):
                continue
            parts = line.strip().split('\t')
            feature_type = parts[2]
            if feature_type in ["CDS", "exon"]:  # Consider CDS and exon features
                attributes_str = parts[8]
                attributes = parse_attributes(attributes_str)
                
                if attributes.get("gene_biotype") == "protein_coding":
                    gene_id = attributes.get("gene_id")
                    transcript_id = attributes.get("transcript_id")
                    
                    # Initialize gene and transcript if not present
                    if gene_id not in cds_lengths:
                        cds_lengths[gene_id] = {}
                    if transcript_id not in cds_lengths[gene_id]:
                        cds_lengths[gene_id][transcript_id] = 0
                    
                    # Add exon length to the CDS length
                    if feature_type == "CDS":
                        exon_length = int(parts[4]) - int(parts[3]) + 1
                        cds_lengths[gene_id][transcript_id] += exon_length
    
    # Find the longest CDS for each gene
    longest_cds = {}
    for gene_id, transcripts in cds_lengths.items():
        longest_transcript_id = max(transcripts, key=transcripts.get)
        longest_cds[gene_id] = {"transcript_id": longest_transcript_id, "length": transcripts[longest_transcript_id]}
    
    return longest_cds

longest_cds_dict = {}

for gtf_file in gtf_files:
    longest_cds = find_longest_cds(gtf_file)
    base_name = os.path.basename(gtf_file).replace('.gtf.gz', '')
    longest_cds_dict[base_name] = {gene_id: data["transcript_id"] for gene_id, data in longest_cds.items()}

# Display the results or process them further as needed


In [27]:
import pickle

In [28]:
# Load sequences_dict from the pickle file
input_file = 'sequences_dict_longest_isoforms.pkl'
with open(input_file, 'rb') as f:
    sequences_dict = pickle.load(f)

In [44]:
from Bio import SeqIO
from Bio.Seq import Seq
import glob
import os

# Assuming longest_cds_dict and sequences_dict are defined elsewhere in your code

# Define the path to the protein FASTA files
protein_fasta_path = '../data/platyhelminthes_dataset_vfinal/*.protein.longest_isoforms.faa'
protein_fasta_files = glob.glob(protein_fasta_path)

# Dictionary to hold the comparison results
comparison_results = {}

for protein_fasta_file in protein_fasta_files:
    # Extract the base name to match with keys in longest_cds_dict
    base_name = os.path.basename(protein_fasta_file)
    base_name = base_name.replace('.protein.longest_isoforms.faa', '.canonical_geneset')

    if base_name in longest_cds_dict:
        cds_ids = longest_cds_dict[base_name]

        for record in SeqIO.parse(protein_fasta_file, "fasta"):
            protein_id = record.id
            if protein_id in cds_ids:
                cds_seq_id = cds_ids[protein_id]
                if cds_seq_id in sequences_dict:
                    cds_seq_record = sequences_dict[cds_seq_id]
                    translated_cds_seq = cds_seq_record.seq.translate(to_stop=True)
                    
                    # Populate the comparison_results dictionary
                    comparison_results[protein_id] = (translated_cds_seq == record.seq)

# Now, comparison_results dictionary contains the results of comparisons for each protein ID


/home/mauricio/anaconda3/envs/r-environment/lib/python3.6/site-packages/Bio/Seq.py:2338: BiopythonWarning: Partial codon, len(sequence) not a multiple of three. Explicitly trim the sequence or add trailing N before translation. This may become an error in future.
  BiopythonWarning,


In [46]:
set(list(comparison_results.values()))

{True}

In [48]:
code2CDSfile = {x.rpartition('/')[2].split('.')[0].split('_')[0].capitalize()[0]+x.rpartition('/')[2].split('.')[0].split('_')[1][0:3]:x for x in glob.glob('../data/platyhelminthes_dataset_vfinal/*.WBPS18.CDS_transcripts.fa.gz')}

In [49]:
targets = [x.rpartition('/')[2].split('.')[0]+'_'+x.rpartition('/')[2].split('.')[1] for x in glob.glob('../data/platyhelminthes_dataset_vfinal/*longest*')]


In [38]:
import glob, gzip, tqdm, pickle
from Bio import SeqIO

In [25]:
# Step 1: Create a dictionary record.name to record for sequences
# only conserve sequences with record.id in original2new['Original Name'].to_list()
sequences_dict = {}
for file_path in tqdm.tqdm(glob.glob('../data/platyhelminthes_dataset_vfinal/*CDS*')):
    with gzip.open(file_path, 'rt') as f:
        for record in SeqIO.parse(f, 'fasta'):
            if record.id in original2new['Original Name'].to_list():
                sequences_dict[record.name] = record

100%|██████████| 21/21 [36:32<00:00, 104.39s/it]


In [28]:
# Save sequences_dict as a pickle file
output_file = 'sequences_dict_longest_isoforms.pkl'
with open(output_file, 'wb') as f:
    pickle.dump(sequences_dict, f)


In [39]:
# Load sequences_dict from the pickle file
input_file = 'sequences_dict_longest_isoforms.pkl'
with open(input_file, 'rb') as f:
    sequences_dict = pickle.load(f)

In [47]:
file_to_protein_transcript_dict.keys()

dict_keys([None, 'Mcor'])

In [ ]:
# go over the keys of file_to_protein_transcript_dict
# the species_name is get with the dictionary code2species
# the file path is retrieved from code2CDSfile
# start a list to store CDS sequences
# if a key is in original2new['Original Name'].to_list(), then retrieve the corresponding transcript from the dictionary that is stored in the values of the iterated dictionary
# now retrieve the CDS sequence from the dict <sequences_dict>
# rename the record using the table original2new: in ['Original Name'] column is the original protein id, and in ['New Name'] the employed new code; if a CDS corresponds to that protein ID, same New Name should be used
# get all things as record.name, description and rest to ''
# save the resulting list of CDS sequences into a filepath that is retrieved using the code2species to get a code (using it to create a reverse dict, and using species_name as key), and then using code2CDSfile dict and replacing '.fa.gz' with ''.longest_isoforms.fna'; if the file already exists, delete it

In [62]:
original2new

Original Name    New Name
0       TsM_000000100      Tsol.1
1       TsM_000000200      Tsol.2
2       TsM_000000300      Tsol.3
3       TsM_000000400      Tsol.4
4       TsM_000000500      Tsol.5
...               ...         ...
304155     T265_16376  Oviv.16375
304156     T265_16377  Oviv.16376
304157     T265_16378  Oviv.16377
304158     T265_16379  Oviv.16378
304159     T265_16380  Oviv.16379

[304160 rows x 2 columns]

In [60]:
# go over keys and items of longest_cds_dict
# the output fasta file is get from '../data/platyhelminthes_dataset_vfinal/'+ {key}.replace('canonical_geneset', 'longest_CDS.transcripts.fna')
# get the values (which are the CDS IDs), and retrieve the corresponding sequences from the sequences_dict
# rename record.id using the original2new table, taking into account that the New Name column has the needed ID
# other descriptors, such as record.name or else, should be set to ''
# in each case, output a FASTA to the corresponding output fasta file

'../data/platyhelminthes_dataset_vfinal/macrostomum_lignano.PRJNA371498.WBPS18.longest_CDS.transcripts.fna'

In [65]:
from Bio import SeqIO
import os
import pandas as pd
import tqdm
import re

# Convert DataFrame to a dictionary for faster access
original_to_new_dict = pd.Series(original2new['New Name'].values,index=original2new['Original Name']).to_dict()

base_directory = '../data/platyhelminthes_dataset_vfinal/'

def get_numeric_id(record):
    """
    Extracts the numeric part of the SeqRecord ID.
    Assumes ID format is '<species_code>.<number>'.
    """
    match = re.search(r'\.(\d+)$', record.id)
    return int(match.group(1)) if match else 0

for key, cds_ids in tqdm.tqdm(longest_cds_dict.items()):
    output_fasta_file = os.path.join(base_directory, f"{key.replace('canonical_geneset', 'longest_CDS.transcripts')}.fna")
    seq_records = []
    for cds_id in cds_ids.values():
        if cds_id in sequences_dict:
            record = sequences_dict[cds_id]
            # Use the pre-constructed dictionary for fast look-up
            if cds_id in original_to_new_dict:
                new_name = original_to_new_dict[cds_id]
                record.id = new_name
                record.name = ''
                record.description = ''
            seq_records.append(record)

    # Sort records by the numeric part of the ID
    seq_records_sorted = sorted(seq_records, key=get_numeric_id)

    with open(output_fasta_file, "w") as output_handle:
        SeqIO.write(seq_records_sorted, output_handle, "fasta")


100%|██████████| 21/21 [00:03<00:00,  5.36it/s]


# Homologues group inference
This was done running the following line in the data folder:

In [9]:
# moving the clusters
import os, pandas as pd, glob, shutil, tqdm

In [11]:
# create folder
#os.mkdir('../results/homolog_groups_data')
#os.mkdir('../results/homolog_groups')

In [7]:
import os, tqdm
import shutil

# Source directory
source_directory = '../data/platyhelminthes_dataset_homologues/schistosomahaematobium_f0_0taxa_algOMCL_e0_C75_S40_'
# Destination directory
destination_directory = '../results/homolog_groups'
# Counter for file names
counter = 1
# List files in the source directory
files = os.listdir(source_directory)
# Iterate through the files and move them to the destination directory with new names
for file in tqdm.tqdm(files):
    source_path = os.path.join(source_directory, file)
    destination_path = os.path.join(destination_directory, f'F{counter}.faa')
    # Move the file
    shutil.move(source_path, destination_path)
    # Increment counter
    counter += 1

0it [00:00, ?it/s]


# Alignment and tree inference

In [14]:
import os
import glob
import tqdm
from concurrent.futures import ThreadPoolExecutor
from Bio import SeqIO

# Define a function to execute muscle command
def run_muscle(homolog_group):
    HG_name = homolog_group.rpartition('/')[2].rpartition('.')[0]
    aln_name = f'../results/alignments/{HG_name}.aln'
    if not os.path.exists(aln_name):
        # Check number of records
        num_records = sum(1 for record in SeqIO.parse(homolog_group, 'fasta'))
        if num_records >= 2:
            if not os.path.exists(aln_name):
                os.system(f"muscle -maxiters 1 -diags -sv -distance1 kbit20_3 -in {homolog_group} -out {aln_name}")

# Get list of homolog groups
homolog_groups = glob.glob('../results/homolog_groups/*')

# Use ThreadPoolExecutor for parallel execution
with ThreadPoolExecutor() as executor:
    # Map the function to the list of homolog groups
    list(tqdm.tqdm(executor.map(run_muscle, homolog_groups), total=len(homolog_groups)))


100%|██████████| 131692/131692 [00:12<00:00, 10544.97it/s] 


In [15]:
os.mkdir('../results/phylogenetic_trees/')

In [13]:
os.chdir('../notebooks/')

In [14]:
os.getcwd()

'/mnt/Disco1/mauricio_PROYECTOS/PEIPER_PLATYS/platyhelminthes_inparalogs/notebooks'

In [18]:
%%bash

# Function to process each alignment file
run_iqtree2() {
    alignment_file="$1"
    # Count the number of sequences in the alignment file
    num_sequences=$(grep -c "^>" "$alignment_file")
    # Only process the alignment file if it has more than 5 sequences
    if [ "$num_sequences" -gt 5 ]; then
        # Extract the HG_name from the alignment file name
        HG_name=$(basename "$alignment_file" | cut -d '.' -f 1)
        # Define the tree folder path
        tree_folder="../results/phylogenetic_trees_vfinal/$HG_name"
        # Create the tree folder if it doesn't exist
        mkdir -p "$tree_folder"
        # Run iqtree2 command
        iqtree2 -s "$alignment_file" -m TEST --threads-max 32 --alrt 1000 --ufboot 1000 --prefix "../results/phylogenetic_trees_vfinal/$HG_name/$HG_name"
    else
        echo "Skipping alignment file $alignment_file: Number of sequences is less than or equal to 5"
    fi
}

# Function to export run_iqtree2 so it's available in parallel
export -f run_iqtree2

# Get a list of alignment files
alignment_files="../results/alignments_final/*.aln"

# Run the processing of alignment files in parallel using GNU Parallel
parallel -j 32 run_iqtree2 ::: $alignment_files


Skipping alignment file ../results/alignments_final/F100016.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100035.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100036.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100057.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100063.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100115.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100122.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100129.aln: Number of sequences is less than or equal to 5
Skipping alignment file ../results/alignments_final/F100142.aln: Number of sequences is less than or equ

environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command not found
environment: line 6: iqtree2: command no

CalledProcessError: Command 'b'\n# Function to process each alignment file\nrun_iqtree2() {\n    alignment_file="$1"\n    # Count the number of sequences in the alignment file\n    num_sequences=$(grep -c "^>" "$alignment_file")\n    # Only process the alignment file if it has more than 5 sequences\n    if [ "$num_sequences" -gt 5 ]; then\n        # Extract the HG_name from the alignment file name\n        HG_name=$(basename "$alignment_file" | cut -d \'.\' -f 1)\n        # Define the tree folder path\n        tree_folder="../results/phylogenetic_trees_vfinal/$HG_name"\n        # Create the tree folder if it doesn\'t exist\n        mkdir -p "$tree_folder"\n        # Run iqtree2 command\n        iqtree2 -s "$alignment_file" -m TEST --threads-max 32 --alrt 1000 --ufboot 1000 --prefix "../results/phylogenetic_trees_vfinal/$HG_name/$HG_name"\n    else\n        echo "Skipping alignment file $alignment_file: Number of sequences is less than or equal to 5"\n    fi\n}\n\n# Function to export r

In [12]:
import os
import glob
import tqdm
import concurrent
import concurrent.futures
from Bio import AlignIO

# Function to process each alignment file
def run_iqtree2(alignment_file):
    try:
        # Read the alignment file and count the number of sequences
        alignment = AlignIO.read(alignment_file, "fasta")
        num_sequences = len(alignment)
        # Only process the alignment file if it has more than 5 sequences
        if num_sequences > 5:
            HG_name = alignment_file.rpartition('/')[2].rpartition('.')[0]
            # Define the tree folder path
            tree_folder = f'phylogenetic_trees_vfinal/{HG_name}'
            # Create the tree folder if it doesn't exist
            os.mkdir(tree_folder)
            # Run iqtree2 command
            %system iqtree2 -s {alignment_file} -m TEST --threads-max 32 --alrt 1000 --ufboot 1000 --prefix phylogenetic_trees_vfinal/{HG_name}/{HG_name}
    except Exception as e:
        print(f"Error inferring phylogeny for alignment {alignment_file}: {str(e)}")
        HG_name = alignment.rpartition('/')[2].rpartition('.')[0]
        if os.path.exists(f'../results/phylogenetic_trees_vfinal/{HG_name}'):
            %system rm -r ../results/phylogenetic_trees_vfinal/{HG_name}

# Get a list of alignment files
alignment_files = glob.glob('alignments_final/*.aln')

# Use ThreadPoolExecutor for parallel execution
with concurrent.futures.ThreadPoolExecutor(max_workers=32) as executor:
    # Map the function to the list of alignment files
    executor.map(run_iqtree2, alignment_files)


Error inferring phylogeny for alignment alignments_final/F10242.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F10242'
Error inferring phylogeny for alignment alignments_final/F658.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F658'Error inferring phylogeny for alignment alignments_final/F105570.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F105570'

Error inferring phylogeny for alignment alignments_final/F14867.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F14867'Error inferring phylogeny for alignment alignments_final/F62076.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F62076'

Error inferring phylogeny for alignment alignments_final/F31443.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F31443'
Error inferring phylogeny for alignment alignments_final/F102863.aln: [Errno 17] File exists: 'phylogenetic_trees_vfinal/F102863'
Error inferring phylogeny for alignment alignments_final/F5711.aln: [Errno 17] File exists: 'phylogeneti

KeyboardInterrupt: 

## Creating dummy trees for one-species-groups
If a homologous group is conformed only by one species, then by definition their members are inparalogs. If these groups are of size n=2, n=3 or n=4 no tree can be inferred, but they dummy trees can be created in order to input them into the analyses.

In [16]:
from ete3 import Tree
import glob
from Bio import SeqIO

In [17]:
# defining used species_codes
species_codes = [x.rpartition('/')[2].split('.')[0].split('_')[0].title()[0]+x.rpartition('/')[2].split('.')[0].split('_')[1][0:3] for x in glob.glob('../data/platyhelminthes_dataset/*.faa')]

In [18]:
import os
import glob
from ete3 import Tree

alignment_dir = '../results/alignments'
output_dir = '../results/phylogenetic_trees'

for aln_file in glob.glob(os.path.join(alignment_dir, '*')):
    # Get record ids in the alignment
    with open(aln_file, 'r') as f:
        alignment = f.readlines()

    record_ids = set()
    for line in alignment:
        if line.startswith('>'):
            record_id = line.strip().split()[0][1:]  # remove '>' and split by space
            record_ids.add(record_id)

    # If the alignment has 2, 3 or 4 sequences, continue analyzing
    if (3 <= len(record_ids) <= 4) or (len(record_ids) == 2):
        # Get set of species in the alignment
        species_set = set([record.split('.')[0] for record in record_ids])

        # If only one species is present, create a dummy Tree with ete3
        if len(species_set) == 1:
            tree = Tree()
            for record in record_ids:
                tree.add_child(name=record) 

            # Get the homologs family name
            homolog_family_name = os.path.splitext(os.path.basename(aln_file))[0]

            # Export the dummy tree
            output_folder = os.path.join(output_dir, homolog_family_name)
            os.makedirs(output_folder, exist_ok=True)
            output_tree_path = os.path.join(output_folder, f"{homolog_family_name}.tree")
            tree.write(outfile=output_tree_path)

            print(f"Dummy tree created for {homolog_family_name} in {output_tree_path}")


Dummy tree created for F120847 in ../results/phylogenetic_trees/F120847/F120847.tree
Dummy tree created for F115512 in ../results/phylogenetic_trees/F115512/F115512.tree
Dummy tree created for F71638 in ../results/phylogenetic_trees/F71638/F71638.tree
Dummy tree created for F2542 in ../results/phylogenetic_trees/F2542/F2542.tree
Dummy tree created for F84327 in ../results/phylogenetic_trees/F84327/F84327.tree
Dummy tree created for F15419 in ../results/phylogenetic_trees/F15419/F15419.tree
Dummy tree created for F124228 in ../results/phylogenetic_trees/F124228/F124228.tree
Dummy tree created for F95150 in ../results/phylogenetic_trees/F95150/F95150.tree
Dummy tree created for F24440 in ../results/phylogenetic_trees/F24440/F24440.tree
Dummy tree created for F54144 in ../results/phylogenetic_trees/F54144/F54144.tree
Dummy tree created for F85906 in ../results/phylogenetic_trees/F85906/F85906.tree
Dummy tree created for F88857 in ../results/phylogenetic_trees/F88857/F88857.tree
Dummy tree